## Project Scrapy

本项目为智能体辅助建筑设计辅助数据

In [3]:
#爬取项目链接
from selenium import webdriver
from selenium.webdriver.chrome.service import Service
from webdriver_manager.chrome import ChromeDriverManager
from selenium.webdriver.common.by import By
import time
import json

all_links = []
driver = webdriver.Chrome()
url = 'https://www.archdaily.cn/search/cn/projects?q=%E5%85%AC%E5%85%B1%E7%A9%BA%E9%97%B4'
driver.get(url)
time.sleep(2) 
dname = 'links.json'

for i in range(100):
    # Find all <a> elements with the desired class and extract the hrefs
    elements = driver.find_elements(By.CSS_SELECTOR, 'a.gridview__content')
    links = [element.get_attribute('href') for element in elements]
    driver.execute_script("window.scrollTo(0, document.body.scrollHeight)")
    time.sleep(2) 
driver.quit()
with open(dname, 'w', encoding='utf-8') as f:
    json.dump(links, f, indent=4)

In [10]:
import json
from bs4 import BeautifulSoup
import requests

datas = {}
index = 1
dname = 'links.json'
maxretry = 10

def fetchint(url):
    for attempt in range(maxretry):
        try:
            response = requests.get(url)
            response.raise_for_status()
            return response
        except(ConnectionError, requests.HTTPError) as e:
            print(f"fail,{e}")
            time.sleep(1)
    print("Fail to connect")
    return None

#links = ["https://www.archdaily.cn/cn/1012701/li-ni-mo-tai-gong-yong-shi-ye-gong-si-dong-tian-jian-zhu-shi-wu-suo-plus-nanometer-architecture?ad_source=search&ad_medium=projects_tab"]
with open(dname, "r") as file:
    links = json.load(file)

for link in links:
#for i in range(200):
    #link = links[i]
    try:
        response = fetchint(link)
        # Check if the request was successful
        if response.status_code == 200:
            # Parse the HTML content of the page
            soup = BeautifulSoup(response.text, 'html.parser')
            
            # Extract elements as needed, for example, all paragraphs
            paragraphs = soup.find_all('p')
        
            bis = ""
            data = {}
            lastpa = ""
            for paragraph in paragraphs:
                if paragraph.text.strip() == "您的文件" or paragraph.text.strip() == "图片" or paragraph.text.strip() == "新闻" or paragraph.text.strip() == "关注主页" or paragraph.text.strip() == "项目" :
                    continue
                if paragraph.text in lastpa:
                    continue
                if "文本描述由建筑师提供" in paragraph.text or "文字说明由建筑师提供" in paragraph.text: 
                    continue
                if paragraph.text.split("！")[0] != "您现在将根据您所关注的内容收到更新":
                    bis = bis + paragraph.text.strip()
                    print(paragraph.text)
                    lastpa = paragraph.text
            data["content"] = bis[3:]

            location = soup.find('div', class_ = "afd-specs__header-location")
            if location:
                data["location"] = location.text
            else:
                data["location"] = ""

            name = soup.find('h1', class_ = "afd-title-big afd-title-big--full afd-title-big--bmargin-big afd-relativeposition")
            if name:
                if len(name.text.split("/")) > 2:
                    data["designer"] = name.text.split("/")[1]
                    data["name"] = name.text.split("/")[0]
                else:
                    data["name"] = name.text.split("/")[0]
                    data["designer"] = name.text.split("/")[0]
            else:
                continue

            infolistt = soup.find("ul", class_ = "afd-char-list afd-specs__item-container js-char-list")
            if infolistt:
                infos = infolistt.find_all('span', class_='afd-specs__value')
            else:
                continue
            if infos:
                # if infos.count == 2:
                #     data['spec'] = infos[1].text #数据在集合中 
                # if infos.count > 2:
                if len(infos) >= 2:
                    data['spec'] = infos[1].text
                else:
                    data["spec"] = "?"
                if len(infos) >= 3:
                    data["year"] = infos[2].find("a").text.strip()
                else:
                    data["year"] = "?"
        
            data["link"] = link
            datas[index] = data
            index += 1
        else:
            print("Failed to retrieve the webpage")
    except Exception as e:
        
        print(f"An error occurred: {e}")
        pass  # This will ignore the error and continue with the next iteration of the loop

   

filename = 'scraped_links.json'
with open(filename, 'w', encoding='utf-8') as f:
    json.dump(datas, f, ensure_ascii=False, indent=4)

+ 28
涧石驿与停云驿位于杭州市滨江区钱塘江南岸，在闻涛路北侧、复兴大桥东北侧，是原作设计工作室承担的杭州市滨江区12公里滨水公共空间改造提升项目的一部分。涧石驿改造自建于2004年的假日花园餐厅，初次踏勘时，建筑顶部网格状的金属屋架和外立面仿石材面砖已经老旧，外露的结构柱由石材包裹，显得较为粗壮。场地北侧为一片假山园林，园林内植被过于繁茂，几乎将假山形态掩盖。站在钱塘江边回望，茂密的植物几乎将主体建筑遮挡。但当我们登上建筑顶层时，四周丰富的景观令人惊喜不已，我们希望将这份独特的视角分享给更多的人。
布局上保留了原建筑一层和半地下空间，而结构上利用原有主体结构的混凝土框架及剪力墙抗侧，将原石材包裹的粗壮圆柱自地坪以上切除，替换为梭形钢结构柱。柱底部采用球铰节点，进一步减小构件的截面尺寸。最后，将原有网格金属屋架拆除，替换以轻薄金属屋面。新屋面根据悬挑梁的受力形式，采用倒T型钢梁，并布置为伞形，实现屋顶结构的大悬挑。钢梁间设置细小的钢管，保证钢梁的稳定，实现建筑立面和俯瞰的完整性效果。依托原有结构和新增钢柱，在建筑不同标高增加景观平台，以提供多层次的长卷式景观视角。
为了充分展现建筑改造后的轻盈效果，也为了叠合历史记忆，原建筑墙面我们选择了颗粒感的肌理涂料替换原有石材面砖。新增部分我们选择了带有反射效果的铝板，以建筑屋面为画板，倒映出四季变化。同时，对场地原有的植物进行梳理，将藤蔓、杂草清理，保留优质灌木、乔木。再根据场地标高，在原有地面之上置入平板体系，形成逐级跌落的观景平台，并结合现场实际情况，为植物预留生长空隙，且保留原有假山石，使其与平台体系融为一体。
意今心的绿植桥梁——低碳桥低碳桥坐落于涧石驿的南侧，杭州市低碳科技馆北侧人工湖的水体中心处。人行桥的铺面石材局部破损、样式陈旧，且台阶踏步较陡，存在安全隐患。为提升该路段人行舒适性和安全性，我们保留原有的人行桥主体，利用加建部分将桥面长度拉长，使得桥身更为舒展，踏步尺度更加宜人。同时选用“中国传统榫卯结构”来进行现代化演绎——依托原有桥体，利用铝合金这一具有现代属性的表皮材料，通过插接搭建，使桥身立面形成多个间隔金属花箱格和点状分布的竖向插板。我们将花箱格内种植绿植，结合点状分布的竖向插板设置夜景照明灯光，实现功能和形式的统一，呈现出极具现代感又具有江南韵味的立面特点。
停云驿改造自建于2004年的荣斋，由西

In [31]:
import pandas as pd

df = pd.read_json("scraped_links.json")
df = df.T
df

content     location  \
1     8涧石驿与停云驿位于杭州市滨江区钱塘江南岸，在闻涛路北侧、复兴大桥东北侧，是原作设计工作室承...       杭州, 中国   
2     1来自建筑师。926工匠博物馆及其所处的926公园，位于钱塘江大桥东南侧，北邻闻涛路，有较好...       杭州, 中国   
3     7杨浦大桥公共空间与综合环境工程位于杨浦区滨江南段区域，跨越杨浦大桥下方、安浦路两侧。一期建...       上海, 中国   
4     7原金威啤酒厂建于上世纪90年代初，位于深圳经济特区发展起步最早的罗湖区；“金威”也是深圳唯...       深圳, 中国   
5     9北京高碑店西店记忆园区三期H9栋建筑，由Weestar Studio与幸会潮玩两间创意机构...       北京, 中国   
...                                                 ...          ...   
1735  6这条625米长的河滨走廊位于汉堡易北河畔的Niederhafen，是城市防洪系统优化和加固...       汉堡, 德国   
1736  7“隐喻花园” 位于曼谷中央商务区的泰式中国拱门塔（泰国 CC 塔）俯瞰着一片绿地，蓝象烹饪...  Bangkok, 泰国   
1737  2该项目最开始面临的挑战是：要获得科利科湖的全景景观，房子必须布置在一个陡峭的斜坡上（坡度4...    Cunco, 智利   
1738  3周尧昆虫博物馆是以周尧教授命名的博物馆，是目前以个人姓氏命名的亚洲最大的昆虫博物馆。其原址...       宁波, 中国   
1739  1未来居住空间建筑元素的拆散与重组、文本转译、不确定性与复杂度是20世纪末21世纪初文化最显...       巴黎, 法国   

                                        name  \
1                          杭州滨江公共空间·涧石驿与停云驿    
2                         杭州滨江公共空间·926工匠博物馆    
3                        杨浦大桥公共空间与综合环境工程（一期）   
4     深圳粤海城·金啤坊 (原金威啤酒厂) 工业遗存室内部分重点公共空间改造设计    
5                            北京西店记忆H9办公空间设计    
...                                      ...   
1735                      汉堡Niederhafen河滨走廊    
1736                              泰国 CC 塔公园    
1737                                  PR 住宅    
1738                              宁波周尧昆虫博物馆    
1739                    巴黎P公寓，奥斯曼建筑内的‘折叠木块’    

                                    designer                            spec  \
1                          杭州滨江公共空间·涧石驿与停云驿                          1646 m²   
2                         杭州滨江公共空间·926工匠博物馆                          1148 m²   
3                        杨浦大桥公共空间与综合环境工程（一期）                        20510 m²   
4     深圳粤海城·金啤坊 (原金威啤酒厂) 工业遗存室内部分重点公共空间改造设计                          1525 m²   
5                            北京西店记忆H9办公空间设计                           900 m²   
...                                      ...                             ...   
1735                      汉堡Niederhafen河滨走廊                      扎哈·哈迪德建筑事务所   
1736                              泰国 CC 塔公园                          1530 m²   
1737                                  PR 住宅   \n\n          2019\n        \n   
1738                              宁波周尧昆虫博物馆                          2986 m²   
1739                    巴黎P公寓，奥斯曼建筑内的‘折叠木块’                           150 m²   

                 year                                               link  
1                2023  https://www.archdaily.cn/cn/1014902/hang-zhou-...  
2                2023  https://www.archdaily.cn/cn/1011551/hang-zhou-...  
3                2022  https://www.archdaily.cn/cn/1009449/yang-pu-da...  
4                2022  https://www.archdaily.cn/cn/1009437/shen-zhen-...  
5                2023  https://www.archdaily.cn/cn/1012347/bei-jing-x...  
...               ...                                                ...  
1735             2019  https://www.archdaily.cn/cn/923385/yi-bao-nied...  
1736             2022  https://www.archdaily.cn/cn/991278/tai-guo-cc-...  
1737  Nicolás Sanchez  https://www.archdaily.cn/cn/974606/pr-zhu-zhai...  
1738             2022  https://www.archdaily.cn/cn/983811/zhu-bo-zhou...  
1739             2020  https://www.archdaily.cn/cn/949822/ba-li-pgong...  

[1739 rows x 7 columns]

In [38]:
#将数据结构处理成line
df.to_json('modified.json', orient='records', lines=True)


# with open(filename, 'r', encoding='utf-8') as file:
#         data = json.load(file)
# # Write the updated data back to the file
# with open(filename, 'w', encoding='utf-8') as file:
#     json.dump(data, file, ensure_ascii = False, indent=4)